# Analyse de séries temporelles avec IA

**Marc Buffat** dpt mécanique, UCB Lyon1

![time series](images/time_series.png)



In [ ]:
import tensorflow as tf

In [ ]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
# police des titres
plt.rc('font', family='serif', size='18')
from IPython.display import display,Markdown
# IA
import sklearn as sk
import tensorflow as tf

In [ ]:
_uid_ = 12345
def serie_temp(N,a0=1.0,a1=0.5,a2 = 0.4, a3=0.1):
    # data / jours 
    np.random.seed(_uid_)
    # time series
    Ts = np.array([x for x in np.arange(N)],dtype=int)
    ys = [ a0*np.sin(2*np.pi*x/180) + a1*np.cos(2*np.pi*x/15) \
         + a2*x/360  for x in range(N)] + \
           a3*np.random.normal(size=N,scale=0.2)
    return Ts,ys

## Objectifs 

On étudie un système temporel $Y(t)$ et on souhaite prédire l'évolution du système: i.e.  la prévision de ses futures réalisations en se basant sur ses valeurs passées

Une série temporelle Yt est communément décomposée en tendance, saisonnalité, bruit:

$$Y(t) =T(t)+S(t)+\epsilon(t)$$

- tendance $T(t)$ = évolution à long terme
- saisonnalité $S(t)$ = phénoméne périodique
- bruit $\epsilon(t)$ = partie aléatoire


### méthodes 


**méthodes classiques:** (modélisation de série chro. linéaires):

 - lissages exponentiels, 
 - modèles de régression (régression linéaire, modèles non-paramétriques. . . ), 
 - modèles SARIMA

**utilisation de l'IA:** 

 - random forest, 
 - réseaux de neuronnes récurrents LSTM


## Génération des données

- Série temporelle $Y = Y(t)$
- N mesures à intervalle régulier $\Delta t$
    - tableau de données ys
    
      $$ys[i] = Y(i\Delta t)$$
      
    - tableau ts (pour l'analyse)
    
      $$ts[i] = i\Delta t$$
      
**tests**
   
   1. série périodique simple
   2. serie bi-périodique (modulation)
   3. avec tendance à long terme
   4. avec du bruit

In [ ]:
# construction serie temporelle
# cas periodique le plus simple
Ts,ys = serie_temp(1000,a0=0,a1=0.5,a2=0.0,a3 = 0.)
# cas bi-periodique 
#Ts,ys = serie_temp(1000,a0=1.0,a1=0.5,a2=0.0,a3=0.0)
# + tendance 
#Ts,ys = serie_temp(1000,a0=1.0,a1=0.5,a2=0.2,a3=0.0)
# + bruit
Ts,ys = serie_temp(1000,a0=1.0,a1=0.5,a2=0.2,a3=0.3)

In [ ]:
plt.figure(figsize=(12,8))
plt.subplot(1,2,1)
plt.plot(Ts[:],ys)
plt.xlabel("jour")
plt.title("serie temporelle");
plt.subplot(1,2,2)
plt.plot(Ts[:100],ys[:100])
plt.xlabel("jour")

## préparation des données

**fenêtrage des données:**

choix d'une fenêtre de nav jours précédents pour prédire nap valeurs (i.e. sur nap jours)

  - nav taille de la fenêtre d'histoire (avant)
  - nap taille de la fenêtre prédiction (après)
  - N nbre de fenêtres
  - t0 date de début prédiction


In [ ]:
def dataset(Ts,ys,nav,nap,N,t0):
    # choix d'une fenetre de nav jours précédents pour prédir nap valeurs (i.e. sur nap jours)
    # nav taille de la fenetre d'histoire (avant)
    # nap taille de la fenetre prediction (apres)
    # N nbre de fenetres
    # t0 date de debut prediction
    # 
    t1 = t0 - N - nav -nap
    print(f"apprentissage sur {N} fenetres de {nav}-{nap} jours entre le jour {t1} et {t0}")
    # 
    X  = np.zeros((N,nav))
    y  = np.zeros((N,nap))
    t  = np.zeros(N,dtype=int)
    # construction de la base de données
    for i in range(N):
        X[i,:] = ys[t1+i:t1+i+nav]
        y[i]   = ys[t1+i+nav:t1+i+nav+nap]
        t[i]   = Ts[t1+i+nav]
    return X,y,t

In [ ]:
# N fenetres: de 14 jours -> 7 jours pour prediction à partir du jour t0
nav = 14
nap = 7
#N  = 200
#t0 = 300
N = 400
t0 = 600
X,y,t = dataset(Ts,ys,nav,nap,N,t0)

In [ ]:
X.shape, y.shape, t.shape

In [ ]:
def plot_dataset():
    plt.figure(figsize=(14,6))
    plt.subplot(1,2,1)
    plt.plot(t-nav,X[:,0])
    plt.plot(t,y[:,0])
    plt.xlabel("jour")
    plt.ylabel("y")
    plt.title("data apprentissage")
    plt.subplot(1,2,2)
    plt.plot(np.arange(t[0]-nav,t[0]+nap),ys[t[0]-nav:t[0]+nap],'--')
    plt.plot(np.arange(t[0]-nav,t[0]),X[0,:],'or')
    plt.plot(np.arange(t[0],t[0]+nap),y[0,:],'xg')
    plt.plot(np.arange(t[-1]-nav,t[-1]+nap),ys[t[-1]-nav:t[-1]+nap],'--')
    plt.plot(np.arange(t[-1]-nav,t[-1]),X[-1,:],'or')
    plt.plot(np.arange(t[-1],t[-1]+nap),y[-1,:],'xg')
    plt.xlabel("jour")
    plt.title("first/last window");
    return

In [ ]:
plot_dataset()

## Scikit Learn RandomForest

**“forêt aléatoire” d’arbres de décision**

- prédiction 1 valeur à la fois 

![random forest](images/Random-forest.png)

## Réseau de neurones: LSTM/ RNN

LSTM = Long Short-Term Memory

- réseau RNN récurrent
- fonction activation: évite l'explosion de la sortie (tanh )
- méthode de gradient numérique ($\alpha$ taux d'apprentissage)
    $$ w_{k+1} = w_k - \alpha F_w$$

- **EPOCH** = nbre d'epoques pour l'apprentissage

Le nombre d'époques est un hyperparamètre qui définit le nombre de fois que l'algorithme d'apprentissage parcours l'ensemble des données d'entraînement



1. Modèle de neuronne informatique

<img src=images/neuroneformel-1.png width="600">

la sortie $y$ est une fonction non linéaire des entrées (f = fonction d'activation)

$$ y = f(\sum_i w_i x_i + b) $$

les coefficients $w_i, b$ sont obtenu par minimisation d'une erreur $Err = || y_{pred} - \hat{y} ||$
à partir d'une base de données d'apprentissage $\hat{y}$ en utilisant des algorithmes de minimisation (gradient)

2. Réseau de neuronnes par couche

<img src=images/reseau_neuronne.png width="600">

3. Réseau de neuronnes récurrents (traitement de séquence temporelle)

<img src=images/reseau-RNN.png width="600">

$$ y^t = f(\sum_i w_i x^t_i + b + \sum_j r_j y^t_j) $$

### Réseaux RNN

![images/Architecture-RNN.jpg](images/Architecture-RNN.jpg)

### La problématique de l'apprentissage d'un réseau récurrent

**réseau récurrent simple classique**  constitué d'une couche récurrente suivie d'une couche dense :

<img src="images/RNNsimple.png" width="200">

Il comprend trois matrices de poids :  W,  R et  V ;  R étant la matrice des poids récurrents. L'apprentissage du réseau consiste donc à apprendre ces trois matrices sur une base d'exemples étiquetés.

Or l'algorithme de minimisation par gradient pour les réseaux de neuronnes utilise un algorithme appelé rétropropagation du gradient. Cet algorithme rétropropage le gradient de l'erreur à travers les différentes couches de poids du réseau, en remontant de la dernière à la première couche.

Malheureusement, dans le cas des réseaux récurrents, la présence du cycle de récurrence (matrice R) interdit l'utilisation de cet algorithme



### solution : rétropropagation à travers le temps

La solution à ce problème consiste à exploiter la version dépliée du réseau, qui élimine les cycles.

Nous allons donc utiliser une approximation du réseau récurrent par un réseau déplié  K fois (K = profondeur = nbre de couches internes cachés de 10 a 100) , comme présenté sur la figure suivante  avec K=2 :

<img src="images/RNNdeplie.png" width="200">

**Attention**

- Le réseau déplié étant plus profond, la disparition du gradient (ou gradient évanescent) est plus importante durant l'apprentissage, et il est plus difficile à entraîner à cause d'une erreur qui tend à s'annuler en se rapprochant des couches basses.

Il est donc important d'utiliser toutes les stratégies possibles permettant de lutter contre ce phénomène : Batch Normalization, dropout, régularisation L1 et L2, etc.

- Comme les poids de la couche récurrente sont dupliqués, les réseaux récurrents sont également sujets à un autre phénomène appelé explosion du gradient. Il s'agit d'un gradient d'erreur dont la norme est supérieure à 1.

Une méthode simple et efficace pour éviter cela consiste à tester cette norme, et à la limiter si elle est trop importante (aussi appelée gradient clipping, en anglais).

### neuronne  LSTM : Long Short Term Memory

Afin de modéliser des dépendances à très long terme, il est nécessaire de donner aux réseaux de neurones récurrents la capacité de maintenir un état sur une longue période de temps.

C'est le but des cellules LSTM (Long Short Term Memory), qui possèdent une mémoire interne appelée cellule (ou cell). La cellule permet de maintenir un état aussi longtemps que nécessaire. Cette cellule consiste en une valeur numérique que le réseau peut piloter en fonction des situations.


<img src="images/RNN_LSTM.png" width="600">


la cellule mémoire peut être pilotée par trois portes de contrôle qu'on peut voir comme des vannes :

   - la porte d'entrée décide si l'entrée doit modifier le contenu de la cellule 

   - la porte d'oubli décide s'il faut remettre à 0 le contenu de la cellule 

   - la porte de sortie décide si le contenu de la cellule doit influer sur la sortie du neurone
   
Le mécanisme des trois portes est strictement similaire. L'ouverture/la fermeture de la vanne est modélisée par une fonction d'activation f qui est généralement une sigmoïde. Cette sigmoïde est appliquée à la somme pondérée des entrées, des sorties et de la cellule, avec des poids  spécifiques. 

Pour calculer la sortie $y^t$, on utilise donc l'entrée $x^t$, les états cachés $h^{t-1}$ ($x^{t-1},x^{t-2}$) (dépliement de la récurrence) qui représentent la mémoire à court terme (short-term mémory) et les états des cellules mémoires $c^{t-1}$  qui représentent la mémoire à long terme (long-term memory)

Comme n'importe quel neurone, les neurones LSTM sont généralement utilisés en couches. Dans ce cas, les sorties de tous les neurones sont réinjectées en entrée de tous les neurones.

Compte tenu de toutes les connexions nécessaires au pilotage de la cellule mémoire, les couches de neurones de type LSTM sont deux fois plus "lourdes" que les couches récurrentes simples, qui elles-mêmes sont deux fois plus lourdes que les couches denses classiques.

**Les couches LSTM sont donc à utiliser avec parcimonie !**

## Mise en oeuvre

### Apprentissage RandomForest

   - scikit learn 

In [ ]:
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.metrics   import r2_score
# choix de l'algorithme
clf = RandomForestRegressor()
#clf = KNeighborsRegressor()
#clf = LinearRegression()
Xlearn = X.copy()
ylearn = y[:,0]
clf.fit(Xlearn,ylearn)

In [ ]:
print("score = {:2d}%".format(int(100*clf.score(Xlearn, ylearn))))
yp = clf.predict(Xlearn)
print("R2 = {:3.2f}%".format(r2_score(ylearn,yp)))

In [ ]:
def plot_pred():
    plt.figure(figsize=(10,6))
    plt.plot(Ts[t2:t2+nap],ypred,'x')
    plt.plot(Ts[t2-nav:t2],Xpred[0],'--o')
    plt.plot(Ts[t2-nav:t2+nap],ys[t2-nav:t2+nap],'--')
    plt.xlabel("jour")
    plt.title(f"prediction sur {nap} jours à partir du jour {t2}");
    return

In [ ]:
# prediction à partir de t2
t2 = t0 
Xpred  = np.array([ys[t2-nav:t2]])
ypred  = np.zeros(nap)
Xp     = Xpred.copy()
ypred[0] = clf.predict(Xp)[0]
for i in range(1,nap):
    Xp[0,:-i] = Xpred[0,i:]
    Xp[0,-i:] = ypred[:i]
    ypred[i] = clf.predict(Xp)[0]
Xpred.shape, ypred.shape

In [ ]:
plot_pred()

### Mise en oeuvre LSTM RNN

 - bibliothèque **tensor flow** Keras RNN

In [ ]:
#Machine learning
from sklearn import preprocessing
import tensorflow as tf
import statsmodels as st
from statsmodels.tsa.seasonal import STL
from sklearn.model_selection  import train_test_split

In [ ]:
Xlearn = X.copy()
ylearn = y.copy()
Xlearn = Xlearn.reshape(X.shape[0], nav, 1)
ylearn = ylearn.reshape(y.shape[0], nap, 1)
Xlearn.shape, ylearn.shape

In [ ]:
#Nombre d'époque d'entrainement (fenetre de taille nav)
#EPOQUE = 300
EPOQUE = 200
#EPOQUE = 50
# modèle du réseaux de neurones(4 rangées (100,100,50,50) dont la première LSTM)
# si pas activation: activation='linear' lineaire a(x)=x, sinon test avec 'relu'
modele_lstm = tf.keras.models.Sequential([
    tf.keras.layers.LSTM(nav),
    tf.keras.layers.Dense(nav,activation='tanh'),
    tf.keras.layers.Dense(nap,activation='tanh'),
    tf.keras.layers.Dense(nap)
])
#Configuration du modèle(on minimise avec la méthode des moindres carrés)
modele_lstm.compile(optimizer='adam', metrics=['mae'], loss='mse')
print(EPOQUE)

In [ ]:
#Lance l'entrainement du modèle
import time
time_start = time.time()
modele_lstm.fit(Xlearn, ylearn, epochs=EPOQUE, verbose = True)
print('phase apprentissage: {:.2f} seconds'.format(time.time()-time_start))

In [ ]:
modele_lstm.summary()

In [ ]:
ypred = modele_lstm.predict(Xlearn, verbose=True)
print(Xlearn.shape,ypred.shape)
Ylearn = ylearn.reshape(ylearn.shape[0],nap,)
print("R2 score {:.2f}".format(r2_score(Ylearn, ypred)))
print("model evaluate loss/mae")
modele_lstm.evaluate(Xlearn,ylearn)

In [ ]:
# prediction à partir de t2
t2 = t0 
Xpred  = np.array([ys[t2-nav:t2]]).reshape(1,nav,1)
ypred = modele_lstm.predict(Xpred, verbose=True)
print(Xpred.shape,ypred.shape)

In [ ]:
Xpred = Xpred.reshape(1,nav,)
ypred = ypred.reshape(nap)
plot_pred()

## bibliographie

- [Initiez-vous au Deep Learning (openclassroom)](https://openclassrooms.com/fr/courses/5801891-initiez-vous-au-deep-learning/)

## FIN